# Parsing Journal of Cognitive Science article data Arthur already scraped (see GDrive)
Aim 1: Parse author & affiliation information for each article.

###### Tentative plans

LOOP THROUGH ALL ROWS: 
- Separate the author and affiliation data
- Create new row for each author in that paper, and denote whether that author was a corresponding author. 
- Also, keep the article name and index (row number) of the article in the original dataset.

In [4]:
import pandas as pd
import string as st

import matplotlib
import numpy as np
from datascience import *
import numpy as np

In [68]:
# Load data CSV -> datascience Table

data_file = '../data/171022_cogsci_journal_unprocessed.csv'
df_pd = pd.read_csv(data_file)

df = Table.read_table(data_file)
index_paperName = Table().with_columns(["Paper Index", df.column(0), "Article Name", df.column(1), "Old Type", df.column(9)])


In [41]:
pd.set_option('display.max_rows', 100)
df_pd.groupby('article_type',sort=True).article_type.count().to_frame().sort_values('article_type',ascending=False)


article_type
article_type                                                    
Original Article                                             593
Regular Articles                                             406
Brief Reports                                                185
Extended Articles                                             55
Issue Information                                             38
Extended Article                                              37
Letters to the Editor                                         24
Cognitive Science News                                        19
Original Articles                                             19
Brief Report                                                  18
Editorial Board                                               17
Author Index                                                  11
Erratum                                                       11
2011 Rumelhart Prize Special Issue Honoring Jud...             9
SPECIAL ISSUE: 2009 Rumelhart Prize Special Iss...             9
Editorial                                                      9
2010 Rumelhart Prize Special Issue Honoring Jam...             9
Letter to the Editor                                           8
Acknowledgement                                                7
Regular articles                                               7
Acknowledgement: Guest Reviewers                               7
Book Review                                                    7
Regular Article                                                6
Contents                                                       6
Reviewer Acknowledgment                                        6
Brief reports                                                  6
Announcement                                                   5
Extended articles                                              5
Subject Index                                                  4
Acknowledgment                                                 3
Acknowledgment: Guest Reviewers                                2
Guest Editorial                                                2
Commentary                                                     2
Comment                                                        2
Introduction                                                   2
Book Reviews                                                   2
Reply                                                          2
Publisher's Note                                               1
Obituary                                                       1
Corrigendum                                                    1
Preface                                                        1
Regular article                                                1
Editorial Note                                                 1
Errata                                                         1
New Editorial Policies                                         1
Special Issue                                                  1
Introduction to the Special Issue                              1
Extended article                                               1
Contents to Volume 7                                           1
SPECIAL ISSUE: 2007 Rumelhart Prize Special Iss...             1
Short Communication                                            1
Contents to Volume 8                                           1
Contents to Volume 12                                          1
Contents to Volume 6                                           1
Contents to Volume 5                                           1
Author Index to Volume 5                                       1
Author Index to Volume 28                                      1
Author Index to Volume 26                                      1
Author Index to Volume 25                                      1
Author Index to Volume 24                                      1
Author Index to Volume

In [42]:
df.show(35)

The 'author_and_details' column in the dataframe contains author and affiliation data.

In [43]:
df_ad = df['authors_and_details'][0:]
df_ad = df_ad
#print(df_ad)

In [44]:
# Test cell
df_ad[2].split('\n')#df['authors_and_details'][2]
#print(range(len(df_ad)))

['Daniel G. Bobrow,Corresponding author             Xerox Palo Alto Research Center/nTerry Winograd             Stanford University']

In [45]:
# create list of lists where the number in each sublist is the article index and the length of the 
# sublist is the number of authors for that article
# - i+1 to counter-act data indexing
df_namesplit = []
df_numauth = []
for i in range(1, len(df_ad)):
        
    temp = df_ad[i].split('/n')
    df_namesplit.append(temp)
    df_numauth.append([i+1]*len(temp))

#print(df_numauth)

In [46]:
# Makes list of lists into single list
finList = []
for i in range(len(df_numauth)):
    for j in range(len(df_numauth[i])):
        finList.append(df_numauth[i][j])
        
#print(finList)

In [47]:
# This function takes a string (author of article ) and strips "Corresponding Author" -> returns stripped string
def clearCorresponding(author):
    result = []
    if ',Corresponding author' in author:

        endIndex = author.find(',')
        result.append(author[:endIndex])
        return result
    
    elif 'Corresponding author' in author:
        endIndex = author.find('Corresponding author')
        
        result.append(author[:endIndex])
        return result
   
    else:
        return author

In [48]:
# Main algorithm to construct table of Articles and Authors

results = Table(make_array("Article Id", "Author", "Department/University", "Corresponding Author"))
# For each sublist in the list of lists df_namesplit
articleCounter = 0 # Used to iterate through list of article id's
for i in range(len(df_namesplit)):
    
    articlesAuthors = df_namesplit[i]
    
    for j in range(len(articlesAuthors)):
        corr_auth = 0
        element = df_namesplit[i][j].split('             ')
        if len(element) > 1: # If the article has an author and the corresponding department/ university
    
            author = clearCorresponding(element[0])
            dept = element[1]
            
            if("Corresponding author" in df_namesplit[i][j]):
                corr_auth = 1
            results = results.with_row([finList[articleCounter],author, dept, corr_auth])
            articleCounter += 1
            
        else:            
            author = clearCorresponding(element[0])
            dept = "NaN"
            
            #newRow = make_array(corr_auth,author, dept)
            results = results.with_row([finList[articleCounter],author, dept, corr_auth])
            articleCounter += 1
            

In [49]:
# Join article name with article id number
results = results.join("Article Id", index_paperName, "Paper Index")
# not sure why we need to drop column 5 twice
results.show()

In [50]:
Extended_Article = ["Extended Articles", "Extended Article", "Extended article", "Extended articles"]
Original_Article = ["Original Article", "Original Articles"]
Regular_Article = ["Regular Articles", "Regular articles", "Regular Article", "Regular article"]
Letter_to_Editor = ["Letters to the Editor","Letter to the Editor"]
Brief_Report = ["Brief Reports", "Brief Report", "Brief reports", "Brief report"]
Announcement = ["Announcement"]
Special = ["2011 Rumelhart Prize Special Issue Honoring Judea Pearl","SPECIAL ISSUE: 2009 Rumelhart Prize Special Issue Honoring Susan Carey","2010 Rumelhart Prize Special Issue Honoring James L. McClelland","SPECIAL ISSUE: 2007 Rumelhart Prize Special Issue Honoring Jeffrey L. Elman Language as a Dynamical System"]
Comment = ["Comment","Short Communication"]
Commentary = ["Commentary"]


In [51]:
def consolidate_Type (oldType):
    if oldType in Extended_Article:
        return "Extended Article"
    if oldType in Original_Article:
        return "Original Article"
    if oldType in Regular_Article:
        return "Regular Article"
    if oldType in Brief_Report:
        return "Brief Report"
    if oldType in Letter_to_Editor:
        return "Letter to Editor"
    if oldType in Announcement:
        return "Announcement"
    if oldType in Special:
        return "Special"
    if oldType in Comment:
        return "Comment"
    if oldType in Commentary:
        return "Commentary"
    return "null"

In [54]:
results = results.with_column("New Type", results.apply(consolidate_Type, "Old Type"))
results = results.drop("Old Type")


ValueError: The column "Old Type" is not in the table. The table contains these columns: Article Id, Author, Department/University, Corresponding Author, Article Name, New Type

In [55]:
results.show(1000)

In [65]:
results2 = Table().with_columns(["Article Id",[], "Author", [], "Department/University", [], "Corresponding Author",[], "Article Name", [], "Type", []])
results2

Article Id | Author | Department/University | Corresponding Author | Article Name | Type

In [67]:

for i in range(results.num_rows):
    if results.column(5)[i] != "null":
        results2 = results2.with_row(results.row(i))  
results2.show()

In [70]:
results2.to_csv("cleaned_data")

In [17]:
# index the row (e.g. 2nd) and split by /n character
df['authors_and_details'][2].split('/n')

['Daniel G. Bobrow,Corresponding author             Xerox Palo Alto Research Center',
 'Terry Winograd             Stanford University']

In [ ]:
# the 0th element contains the information of the first author
df['authors_and_details'][2].split('/n')[0]

In [ ]:
# further split author info to separate name and affiliation
au1 = df['authors_and_details'][2].split('/n')[0].split('             ')

In [ ]:
au1

In [ ]:
# find the corresponding author and delete that part of the string ',Corresponding author'
if 'Corresponding author' in au1[0]:
    endind = au1[0].find(',Corresponding author')
    print(endind)
    print(au1[0][:endind], '- ', au1[1])

In [ ]:
# make a new dataset


### The latter ones have a little more information
Let's go to index 1500

In [ ]:
df['authors_and_details'][1501].split('/n')

In [ ]:
df['article_name'][1501]